In [ ]:
import pandas as pd 
import numpy as np 
import os
from pydub import AudioSegment 
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import librosa
import librosa.display
from IPython.display import Audio
from pydub import AudioSegment
from pydub.playback import play
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from imblearn.over_sampling import RandomOverSampler
from sklearn.mixture import GaussianMixture
from sklearn.metrics import accuracy_score, classification_report
import speaker_verification_toolkit.tools as svt
from tensorflow import keras
from tensorflow.keras import layers  
%matplotlib inline
from tensorflow.keras.models import load_model

: 

In [1]:
# def preprocess_and_plot_audio_librosa(audio_path, noise_threshold=0.02, silence_threshold=0.002):
#     # Load audio file
#     y, sr = librosa.load(audio_path,sr=16000)

#     # Create a time array for plotting
#     t = librosa.frames_to_time(np.arange(len(y)),sr=16000)

#     # Plot the original audio
#     fig = go.Figure()
#     fig.add_trace(go.Scatter(x=t, y=y, mode='lines', name='Original Audio'))
#     fig.update_layout(title_text='Original Audio', xaxis_title='Time (s)', yaxis_title='Amplitude')
#     fig.show()

#     # Remove noise
#     y = svt.rms_silence_filter(y,threshold=silence_threshold)
#     # y = librosa.effects.preemphasis(y)
#     y = librosa.effects.deemphasis(y)
#     y = librosa.effects.deemphasis(y)
#     y = librosa.effects.deemphasis(y)
    
#     # y = librosa.effects.deemphasis(y)
#     # Trim silent portions
#     # yt, index = librosa.effects.trim(y, top_db=silence_threshold)
#     # yt = librosa.feature.mfcc(y=yt, sr=sr, n_mfcc=30)
#     # audio_segment = AudioSegment(y.tobytes(), frame_rate=sr, sample_width=y.dtype.itemsize, channels=1)
#     # play(audio_segment)
#     # Plot the processed audio
#     fig = go.Figure()
#     fig.add_trace(go.Scatter(x=t, y =y, mode='lines', name='Processed Audio'))
#     fig.update_layout(title_text='Processed Audio', xaxis_title='Time (s)', yaxis_title='Amplitude')
#     fig.show()

#     return y,sr,t

In [ ]:
# adi,sr,t = preprocess_and_plot_audio_librosa('sound/adi.wav')
# leepi,sr,t = preprocess_and_plot_audio_librosa('sound/leepi.wav')
# khushi,sr,t = preprocess_and_plot_audio_librosa('sound/khushi.wav')
# # df_adi = pd.DataFrame(adi.T,columns=[f'MFCC_{i+1}'for i in range(adi.shape[0])])


In [2]:
def preprocess_and_extract_mfcc(audio_path, noise_threshold=0.02, silence_threshold=0.002, n_mfcc=20):
    # Load audio file
    y, sr = librosa.load(audio_path,sr=16000)

    # Create a time array for plotting
    t = librosa.frames_to_time(np.arange(len(y)),sr=16000)

    # Plot the original audio
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=t, y=y, mode='lines', name='Original Audio'))
    fig.update_layout(title_text='Original Audio', xaxis_title='Time (s)', yaxis_title='Amplitude')
    fig.show()

    # Remove noise
    y = svt.rms_silence_filter(y,threshold=silence_threshold)
    # y = librosa.effects.preemphasis(y)
    # y = librosa.effects.preemphasis(y)
    y = librosa.effects.deemphasis(y)
    y = librosa.effects.deemphasis(y)
    y = librosa.effects.deemphasis(y)
    
    # y = svt.rms_silence_filter(y,threshold=0.02)
    # Trim silent portions
    # yt, index = librosa.effects.trim(y, top_db=silence_threshold)

    # Extract MFCC features
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=n_mfcc)

    # Create a DataFrame with time and MFCC features
    df = pd.DataFrame(mfcc.T, columns=[f'MFCC_{i+1}' for i in range(n_mfcc)])
    df['Time'] = librosa.frames_to_time(np.arange(len(df)), sr=sr)

    # Plot the processed audio
    fig_mfcc = go.Figure()

    for i in range(1, n_mfcc + 1):
        fig_mfcc.add_trace(go.Scatter(x=df['Time'], y=df[f'MFCC_{i}'], mode='markers', name=f'MFCC_{i}'))

    fig_mfcc.update_layout(title_text='MFCC Points over Time', xaxis_title='Time (s)', yaxis_title='MFCC Values')
    fig_mfcc.show()

    # Plot the processed audio
    fig_processed = go.Figure()
    fig_processed.add_trace(go.Scatter(x=t, y=y, mode='lines', name='Processed Audio'))
    fig_processed.update_layout(title_text='Processed Audio', xaxis_title='Time (s)', yaxis_title='Amplitude')
    fig_processed.show()

    return df

# Example usage
audio_file_path = 'sound/adi.wav'
df_adi = preprocess_and_extract_mfcc(audio_file_path)
df_adi["ID"]='1'
df_adi["Name"]='adi'
audio_file_path = 'sound/leepi.wav'
df_leepi = preprocess_and_extract_mfcc(audio_file_path)
df_leepi["ID"]='2'
df_leepi["Name"]='leepi'
audio_file_path = 'sound/khushi.wav'
df_khushi= preprocess_and_extract_mfcc(audio_file_path)
df_khushi["ID"]='3'
df_khushi["Name"]='khushi'


In [3]:
df_khushi

MFCC_1      MFCC_2      MFCC_3     MFCC_4     MFCC_5     MFCC_6  \
0   143.741658   63.312752   55.440889  44.190018  31.808671  20.515781   
1   178.954950  104.631599   75.481882  40.266297  11.635432  -2.969923   
2   193.038558  120.329690   81.070876  35.702583   1.999006 -11.419578   
3   180.373706  106.258435   76.331766  40.649104  12.151092  -2.229830   
4   162.683475   85.922550   67.418294  43.780556  22.318857   8.183426   
5   172.858026   99.061596   77.287464  49.574357  24.611135   8.451787   
6   207.242323  141.567487  104.421617  59.086152  20.838512  -1.684892   
7   221.892101  158.263094  111.834603  57.939734  16.174397  -5.073362   
8   218.635629  153.430022  106.892265  54.058324  14.755601  -3.752894   
9   213.106391  147.377477  104.803675  55.336996  16.952372  -2.774634   
10  207.545877  142.044550  105.030423  59.753537  21.077879  -2.733293   
11  196.774269  129.931828  100.162370  61.612410  25.607723   0.396017   
12  189.726185  121.161624   94.467728  59.619851  26.629511   2.952226   
13  191.057401  123.793933   98.826282  65.425517  32.365495   6.623519   
14  196.057212  131.465943  107.711126  74.766582  40.207798  10.851511   
15  206.542769  144.265848  115.510282  76.959333  38.112802   6.403797   
16  206.225497  142.540970  112.086570  74.817592  40.040735  11.304438   
17  202.661441  137.492406  107.353848  71.375850  39.035018  13.107698   
18  200.949642  136.759773  109.728661  74.774253  40.443495  11.945019   
19  205.843001  140.173393  104.651002  61.511159  25.180883   3.327573   
20  213.898336  145.069351   96.477616  45.772314  12.844126   1.196204   
21  213.181571  141.891327   91.034219  43.683760  17.304432   7.874798   
22  203.613647  130.276881   84.805311  44.912616  25.071820  17.433409   
23  196.628986  122.714741   82.113543  46.187425  28.343779  21.331444   
24  194.205467  121.547176   85.110691  51.003096  32.202333  24.337577   
25  181.344480  109.103487   84.615030  58.757929  40.337655  28.883434   
26  157.810761   83.284457   75.434261  63.626001  49.481146  34.765882   
27  150.712387   73.302536   65.656590  54.287847  40.920474  27.390862   
28  147.009329   68.003694   60.239754  48.876020  35.862724  23.227482   
29  150.413318   72.722646   64.685853  52.905333  39.379989  26.192402   
30  151.908969   74.544357   65.786982  53.255731  39.379018  26.479920   
31  155.187557   79.137315   70.204677  57.270229  42.699867  28.866937   
32  183.539612  109.767292   78.235965  43.035285  18.703862  10.876938   
33  222.926290  148.947481   84.952696  28.720437   1.076291  -0.877621   
34  215.618154  143.290326   86.441256  31.443111   2.054423   0.031026   
35  178.305974  103.773594   75.344857  42.496012  17.985230   7.751177   
36  151.692996   72.297845   58.857595  41.669555  25.978137  15.379471   

       MFCC_7     MFCC_8     MFCC_9    MFCC_10  ...    MFCC_14    MFCC_15  \
0   11.931237   6.720244   4.546167   4.323646  ...   0.062043  -3.292456   
1   -3.974263   2.211726   7.927430   8.697241  ...  -1.804732   1.054038   
2   -7.891460   1.894685   7.901586   6.484951  ...  -0.992049   2.693565   
3   -3.793813   0.709765   4.359471   4.094255  ...   0.874226   2.435021   
4    2.605207   3.192549   5.848403   7.086148  ...  -4.505438  -5.097293   
5    2.359522   3.155342   5.612224   5.420166  ... -16.166056 -16.487556   
6   -8.974767  -7.621485  -4.773315  -4.139745  ... -11.505013 -14.070238   
7   -9.779393  -7.554927  -5.739945  -6.157916  ...  -9.384516 -12.900725   
8   -7.076894  -5.517608  -5.489415  -7.022361  ...  -4.628931  -9.086766   
9   -7.833336  -7.257395  -7.274267  -8.316934  ...  -3.478352  -7.293165   
10 -11.911671 -11.945687  -8.713857  -5.639443  ...  -7.093274  -9.013089   
11 -11.451328 -12.679016  -8.754287  -4.745378  ...  -6.939051  -6.970588   
12  -8.934406 -11.359826  -9.151302  -6.701988  ...  -7.534861  -7.309061   
13  -8.745654 -14.751262 -14.876607 -12.840397  ...  -7.947859  -7.581039   
14

In [4]:
df = pd.concat([df_adi,df_leepi,df_khushi],ignore_index=True)

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 86 entries, 0 to 85
Data columns (total 23 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   MFCC_1   86 non-null     float64
 1   MFCC_2   86 non-null     float64
 2   MFCC_3   86 non-null     float64
 3   MFCC_4   86 non-null     float64
 4   MFCC_5   86 non-null     float64
 5   MFCC_6   86 non-null     float64
 6   MFCC_7   86 non-null     float64
 7   MFCC_8   86 non-null     float64
 8   MFCC_9   86 non-null     float64
 9   MFCC_10  86 non-null     float64
 10  MFCC_11  86 non-null     float64
 11  MFCC_12  86 non-null     float64
 12  MFCC_13  86 non-null     float64
 13  MFCC_14  86 non-null     float64
 14  MFCC_15  86 non-null     float64
 15  MFCC_16  86 non-null     float64
 16  MFCC_17  86 non-null     float64
 17  MFCC_18  86 non-null     float64
 18  MFCC_19  86 non-null     float64
 19  MFCC_20  86 non-null     float64
 20  Time     86 non-null     float64
 21  ID       86 non-nu

In [6]:
df.Name = (df.Name == 'adi').astype(int)

In [7]:
df.Name.unique()

array([1, 0])

In [8]:
df

MFCC_1      MFCC_2     MFCC_3     MFCC_4     MFCC_5     MFCC_6  \
0   237.712421   91.742629  82.321631  68.547071  52.780710  37.441853   
1   251.317716  109.007892  94.276105  73.478596  51.023603  31.086491   
2   250.695586  107.540439  91.240890  68.412980  44.126578  23.140338   
3   248.259537  104.467808  89.128015  67.442489  44.003449  23.221100   
4   248.207963  104.646367  89.959270  69.065581  46.245938  25.678727   
..         ...         ...        ...        ...        ...        ...   
81  183.539612  109.767292  78.235965  43.035285  18.703862  10.876938   
82  222.926290  148.947481  84.952696  28.720437   1.076291  -0.877621   
83  215.618154  143.290326  86.441256  31.443111   2.054423   0.031026   
84  178.305974  103.773594  75.344857  42.496012  17.985230   7.751177   
85  151.692996   72.297845  58.857595  41.669555  25.978137  15.379471   

       MFCC_7     MFCC_8     MFCC_9   MFCC_10  ...    MFCC_14   MFCC_15  \
0   24.457214  14.901371   8.909772  5.852589  ...   2.873250  1.309555   
1   16.491196   8.135641   5.101603  5.328760  ...   3.962788  1.307297   
2    8.597283   1.365185   0.185984  2.490144  ...   4.538146  1.468534   
3    8.160174  -0.100243  -2.423850 -0.983083  ...   1.549840 -1.513995   
4   10.368032   1.518541  -1.486372 -0.563007  ...   2.574400 -0.267878   
..        ...        ...        ...       ...  ...        ...       ...   
81  14.593465  19.569263  18.009676  9.298662  ...  -1.079291  3.273038   
82  11.986296  23.127135  17.019982 -2.341604  ...  -5.006746 -4.682991   
83  11.703593  19.383696  12.801258 -3.375070  ...  -7.281883 -5.350206   
84   8.910442  13.274237  13.422860  7.096988  ... -10.562325 -5.918973   
85  10.541626   9.490121   9.146087  7.166567  ...  -6.848570 -5.646289   

     MFCC_16   MFCC_17    MFCC_18    MFCC_19    MFCC_20   Time  ID  Name  
0  -0.687042 -2.850072  -4.923463  -6.706571  -8.047201  0.000   1     1  
1  -1.183838 -3.215014  -4.924749  -6.656984  -8.616332  0.032   1     1  
2  -1.524733 -3.987382  -6.015228  -7.993000 -10.183016  0.064   1     1  
3  -4.855302 -7.851507 -10.305513 -12.328313 -14.056391  0.096   1     1  
4  -3.534297 -6.514439  -8.872396 -10.622572 -11.921272  0.128   1     1  
..       ...       ...        ...        ...        ...    ...  ..   ...  
81  3.662305  0.400322  -3.677099  -5.771352  -5.003569  1.024   3     0  
82 -2.233632 -1.997685  -5.296678  -7.947559  -8.342563  1.056   3     0  
83 -4.045089 -4.314948  -6.969472 -10.050486 -11.459583  1.088   3     0  
84 -2.209803 -0.994267  -2.016313  -4.124361  -6.268436  1.120   3     0  
85 -3.264659 -1.330035  -0.851523  -1.746960  -3.080563  1.152   3     0  

[86 rows x 23 columns]

In [9]:
df = df.sample(frac=1).reset_index(drop=True)

In [10]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 86 entries, 0 to 85
Data columns (total 23 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   MFCC_1   86 non-null     float64
 1   MFCC_2   86 non-null     float64
 2   MFCC_3   86 non-null     float64
 3   MFCC_4   86 non-null     float64
 4   MFCC_5   86 non-null     float64
 5   MFCC_6   86 non-null     float64
 6   MFCC_7   86 non-null     float64
 7   MFCC_8   86 non-null     float64
 8   MFCC_9   86 non-null     float64
 9   MFCC_10  86 non-null     float64
 10  MFCC_11  86 non-null     float64
 11  MFCC_12  86 non-null     float64
 12  MFCC_13  86 non-null     float64
 13  MFCC_14  86 non-null     float64
 14  MFCC_15  86 non-null     float64
 15  MFCC_16  86 non-null     float64
 16  MFCC_17  86 non-null     float64
 17  MFCC_18  86 non-null     float64
 18  MFCC_19  86 non-null     float64
 19  MFCC_20  86 non-null     float64
 20  Time     86 non-null     float64
 21  ID       86 non-nu

In [11]:
train ,valid, test = np.split(df, [int(0.6*len(df)),int(0.8*len(df))])

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/numpy/core/fromnumeric.py:59: FutureWarning:

'DataFrame.swapaxes' is deprecated and will be removed in a future version. Please use 'DataFrame.transpose' instead.



In [12]:
def scale_dataset(dataframe, oversample=False):
    # Separate MFCC features from 'Time' and 'ID'
    mfcc_columns = dataframe.columns[:20]
    time_id_columns = dataframe.columns[20:-1]

    X_mfcc = dataframe[mfcc_columns].values
    X_time_id = dataframe[time_id_columns].values
    y = dataframe[dataframe.columns[-1]].values

    scaler_mfcc = StandardScaler()
    X_mfcc_scaled = scaler_mfcc.fit_transform(X_mfcc)

    # Concatenate the scaled MFCC features with 'Time' and 'ID'
    X_scaled = np.hstack((X_mfcc_scaled, X_time_id))

    if oversample:
        ros = RandomOverSampler()
        X_scaled, y = ros.fit_resample(X_scaled, y)

    # Concatenate the oversampled features with the target column
    data = np.hstack((X_scaled, np.reshape(y, (-1, 1))))

    return data.astype('float64'), X_scaled.astype('float64'), y.astype('float64')

In [13]:
train, X_train, y_train = scale_dataset(train, oversample=True)
valid, X_valid, y_valid = scale_dataset(valid, oversample=False)
test, X_test, y_test = scale_dataset(test, oversample=False)

In [14]:
# X_train = X_train.astype('float64')
# valid = valid.astype('float64')
# test = test.astype('float64')
train.dtype

dtype('float64')

In [ ]:
# y_train = y_train.astype(float)


In [ ]:
def train_model(X_train, y_train, num_nodes, dropout_prob, lr, batch_size, epochs):
  nn_model = keras.Sequential([
      keras.layers.Dense(num_nodes, activation='relu', input_shape=(22,)),
      keras.layers.Dropout(dropout_prob),
      keras.layers.Dense(num_nodes, activation='relu'),
      keras.layers.Dropout(dropout_prob),
      keras.layers.Dense(1, activation='sigmoid')
  ])

  nn_model.compile(optimizer=keras.optimizers.legacy.Adam(lr), loss='binary_crossentropy',
                  metrics=['accuracy'])
  history = nn_model.fit(
    X_train, y_train, epochs=epochs, batch_size=batch_size, validation_split=0.2, verbose=0
  )

  return nn_model, history

def train_lstm_model(X_train, y_train, num_nodes, dropout_prob, lr, batch_size, epochs):
    # Add a new axis to the input data to make it 3D
    X_train = X_train[:, :, np.newaxis]

    lstm_model = keras.Sequential([
        layers.LSTM(num_nodes, activation='relu', input_shape=(X_train.shape[1], 1)),
        keras.layers.Dropout(dropout_prob),
        keras.layers.Dense(1, activation='sigmoid')
    ])

    lstm_model.compile(optimizer=keras.optimizers.legacy.Adam(lr), loss='binary_crossentropy', metrics=['accuracy'])
    history = lstm_model.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_split=0.2, verbose=0)

    return lstm_model, history

def train_deep_nn_model(X_train, y_train, hidden_layers, dropout_prob, lr, batch_size, epochs):
    # Flatten the input data
    X_train_flat = X_train.reshape(X_train.shape[0], -1)

    # Define the deep neural network model
    deep_nn_model = keras.Sequential()

    # Add input layer
    deep_nn_model.add(layers.Dense(hidden_layers[0], activation='relu', input_shape=(X_train_flat.shape[1],)))
    deep_nn_model.add(layers.Dropout(dropout_prob))

    # Add hidden layers
    for layer_size in hidden_layers[1:]:
        deep_nn_model.add(layers.Dense(layer_size, activation='relu'))
        deep_nn_model.add(layers.Dropout(dropout_prob))

    # Add output layer
    deep_nn_model.add(layers.Dense(1, activation='sigmoid'))

    # Compile the model
    deep_nn_model.compile(optimizer=keras.optimizers.legacy.Adam(learning_rate=lr),
                          loss='binary_crossentropy',
                          metrics=['accuracy'])

    # Train the model
    history = deep_nn_model.fit(X_train_flat, y_train, epochs=epochs, batch_size=batch_size, validation_split=0.2, verbose=0)

    return deep_nn_model, history

def train_dual_conv_model(X_train, y_train, num_filters, kernel_size, pool_size, num_nodes, dropout_prob, lr, batch_size, epochs):
    model_dual_conv = keras.Sequential([
        layers.Conv1D(num_filters, kernel_size, activation='relu', input_shape=(X_train.shape[1], 1)),
        layers.MaxPooling1D(pool_size=2),
        layers.Conv1D(num_filters, kernel_size, activation='relu'),
        layers.MaxPooling1D(pool_size=2),
        layers.Flatten(),
        layers.Dense(num_nodes, activation='relu'),
        layers.Dropout(dropout_prob),
        layers.Dense(1, activation='sigmoid')
    ])

    model_dual_conv.compile(optimizer=keras.optimizers.legacy.Adam(lr), loss='binary_crossentropy', metrics=['accuracy'])
    history_dual_conv = model_dual_conv.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, validation_split=0.2, verbose=0)

    return model_dual_conv, history_dual_conv


In [ ]:
def plot_history(history):
    fig = go.Figure()

    # Add training loss trace
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history['loss'],
                             mode='lines+markers', name='Training Loss'))

    # Add validation loss trace
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history['val_loss'],
                             mode='lines+markers', name='Validation Loss'))

    # Add training accuracy trace
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history['accuracy'],
                             mode='lines+markers', name='Training Accuracy'))

    # Add validation accuracy trace
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history['val_accuracy'],
                             mode='lines+markers', name='Validation Accuracy'))

    # Update layout
    fig.update_layout(title='Training History',
                      xaxis=dict(title='Epoch'),
                      yaxis=dict(title='Metric Value'),
                      legend=dict(x=0.7, y=1),
                      template='plotly_white')

    fig.show()

In [ ]:
lstm_model, lstm_history = train_lstm_model(X_train, y_train, 16, 0,0.01, 32, 100)
plot_history(lstm_history)
dnn_model, dnn_history = train_deep_nn_model(X_train, y_train, [32], 0.2, 0.01, 32, 100)
plot_history(dnn_history)
dualConv_model, dualConv_history = train_dual_conv_model(X_train, y_train, 64, 3, 4, 64, 0, 0.01, 128, 100)
plot_history(dualConv_history)
nn_model, nn_history = train_model(X_train, y_train, 64, 0,0.01, 32, 100)
plot_history(nn_history)

In [ ]:



least_val_loss = float('inf')
least_loss_model = None
epochs = 100

for num_nodes in [16, 32, 64]:
    for dropout_prob in [0, 0.2]:
        for lr in [0.01, 0.005, 0.001]:
            for batch_size in [32, 64, 128]:
                print(f"{num_nodes} nodes, dropout {dropout_prob}, lr {lr}, batch size {batch_size}")
                model, history = train_lstm_model(X_train, y_train, num_nodes, dropout_prob, lr, batch_size, epochs)
                plot_history(history)
                
                # Reshape validation data before evaluation
                X_valid_reshaped = X_valid[:, :, np.newaxis]
                val_loss = model.evaluate(X_valid_reshaped, y_valid)[0]
                
                if val_loss < least_val_loss:
                    least_val_loss = val_loss
                    least_loss_model = model
                    beast_least_loss_lstm_model= f"{num_nodes} nodes, dropout {dropout_prob}, lr {lr}, batch size {batch_size}"


least_val_loss_deep_nn = float('inf')
least_loss_model_deep_nn = None
epochs = 100

for num_nodes in [16, 32, 64]:
    for dropout_prob in [0, 0.2]:
        for lr in [0.01, 0.005, 0.001]:
            for batch_size in [32, 64, 128]:
                print(f"{num_nodes} nodes, dropout {dropout_prob}, lr {lr}, batch size {batch_size}")
                
                # Train deep neural network model
                model_deep_nn, history_deep_nn = train_deep_nn_model(X_train, y_train, [num_nodes], dropout_prob, lr, batch_size, epochs)
                plot_history(history_deep_nn)
                
                # Flatten validation data before evaluation
                X_valid_flat_deep_nn = X_valid.reshape(X_valid.shape[0], -1)
                val_loss_deep_nn = model_deep_nn.evaluate(X_valid_flat_deep_nn, y_valid)[0]
                
                if val_loss_deep_nn < least_val_loss_deep_nn:
                    least_val_loss_deep_nn = val_loss_deep_nn
                    least_loss_model_deep_nn = model_deep_nn
                    best_least_loss_dnn_model = f"{num_nodes} nodes, dropout {dropout_prob}, lr {lr}, batch size {batch_size}"



least_val_loss_dual_conv = float('inf')
least_loss_model_dual_conv = None
epochs = 100

for num_filters in [32, 64]:
    for kernel_size in [3, 5]:
        for pool_size in [2, 4]:
            for num_nodes in [16, 32, 64]:
                for dropout_prob in [0, 0.2]:
                    for lr in [0.01, 0.005, 0.001]:
                        for batch_size in [32, 64, 128]:
                            print(f"{num_filters} filters, {kernel_size} kernel size, {pool_size} pool size, {num_nodes} nodes, dropout {dropout_prob}, lr {lr}, batch size {batch_size}")

                            # Train dual convolutional model
                            model_dual_conv, history_dual_conv = train_dual_conv_model(X_train, y_train, num_filters, kernel_size, pool_size, num_nodes, dropout_prob, lr, batch_size, epochs)
                            # plot_history(history_dual_conv)

                            # Evaluate on the validation set
                            val_loss_dual_conv = model_dual_conv.evaluate(X_valid, y_valid)[0]

                            if val_loss_dual_conv < least_val_loss_dual_conv:
                                least_val_loss_dual_conv = val_loss_dual_conv
                                least_loss_model_dual_conv = model_dual_conv
                                best_model_info_dual_conv = f"{num_filters} filters, {kernel_size} kernel size, {pool_size} pool size, {num_nodes} nodes, dropout {dropout_prob}, lr {lr}, batch size {batch_size}"
                                

In [ ]:
lstm_y_pred = lstm_model.predict(X_test)
lstm_y_pred = (lstm_y_pred > 0.5).astype(int).reshape(-1,)
nn_y_pred = nn_model.predict(X_test)
nn_y_pred = (nn_y_pred > 0.5).astype(int).reshape(-1,)
dnn_y_pred = dnn_model.predict(X_test)
dnn_y_pred = (dnn_y_pred > 0.5).astype(int).reshape(-1,)
dualConv_y_pred = dualConv_model.predict(X_test)
dualConv_y_pred = (dualConv_y_pred > 0.5).astype(int).reshape(-1,)

In [ ]:
accuracy = accuracy_score(y_test, lstm_y_pred)
report = classification_report(y_test, lstm_y_pred)

print(f'Accuracy: {accuracy}')
print('Classification Report:')
print(report)
accuracy = accuracy_score(y_test, dnn_y_pred)
report = classification_report(y_test, dnn_y_pred)

print(f'Accuracy: {accuracy}')
print('Classification Report:')
print(report)
accuracy = accuracy_score(y_test, nn_y_pred)
report = classification_report(y_test, nn_y_pred)

print(f'Accuracy: {accuracy}')
print('Classification Report:')
print(report)
accuracy = accuracy_score(y_test, dualConv_y_pred)
report = classification_report(y_test, dualConv_y_pred)

print(f'Accuracy: {accuracy}')
print('Classification Report:')
print(report)

In [ ]:
least_loss_model_deep_nn.save("dnn_model.h5")

In [ ]:
least_loss_model_dual_conv.summary()

In [ ]:
best_least_loss_dnn_model

In [ ]:
best_model_info_dual_conv

In [ ]:
beast_least_loss_lstm_model

In [ ]:
best_least_loss_nn_model